In [1]:
import os; os.chdir('..')

In [2]:
import pandas as pd

from datasets import Dataset, load_dataset

/home/ubuntu/SentenceStructureComparision/venv/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [3]:
df= pd.read_csv('data_categories/Final_Category_Data_With_Labels.csv')


df.sample(10)

category  \
3982   Citation context relevance assessment platforms   
24651                                Geology fieldwork   
28113              Password management for individuals   
10999                    Real estate market statistics   
17096                           Running gear for women   
2374                             Sports Team Fan Pride   
9932                              Wine and food events   
2953           College admissions for aspiring dancers   
25038       Software development best practices forums   
29703                         Quantum physics theories   

                           label  label_id  
3982                   Reference        12  
24651                    Science         2  
28113  Computers_and_Electronics         7  
10999                Real Estate        24  
17096         Beauty_and_Fitness         9  
2374                      Sports        26  
9932              Food_and_Drink        15  
2953          Jobs_and_Education        21  
25038         Online Communities         8  
29703                    Science         2

In [4]:
df_new= df[['category', 'label_id']]
df_new.head()

category  label_id
0                         Internet usage monitoring        25
1            Food safety guidelines and regulations        15
2  Internet protocols and edge computing in finance        25
3                           Online grocery shopping        15
4          Writing retreats for poets and novelists        17

In [5]:
df_new.duplicated().value_counts() # 10837 duplicate values

False    22474
True     11138
Name: count, dtype: int64

In [6]:
df_new.rename(
    columns={
    "category": "text", 
    "label_id": "label"
}, 
          inplace=True
)

df_new.sample(10)

/tmp/ipykernel_139501/984288843.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_new.rename(


text  label
2925                       Kids' toy stores online     13
31108          Birdwatching apps for bird behavior      5
6817                            Legal developments      1
20037  Citation context relevance assessment tools     12
18928                            Orchid care guide     20
33358         Scientific publications and journals      2
16499                        Service dog etiquette      5
26484                 Social media trends analysis     25
15543              Troubleshooting computer issues      7
15854                                        large     23

In [7]:
dataset_df= Dataset.from_pandas(df_new)
dataset_df

/home/ubuntu/SentenceStructureComparision/venv/lib/python3.10/site-packages/pyarrow/pandas_compat.py:373: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if _pandas_api.is_sparse(col):


Dataset({
    features: ['text', 'label'],
    num_rows: 33612
})

In [8]:
new_data= dataset_df.train_test_split(test_size=0.2)
new_data

DatasetDict({
    train: Dataset({
        features: ['text', 'label'],
        num_rows: 26889
    })
    test: Dataset({
        features: ['text', 'label'],
        num_rows: 6723
    })
})

In [9]:
from transformers import AutoTokenizer

tokenizer = AutoTokenizer.from_pretrained("distilbert-base-uncased")

In [10]:
def preprocess_function(examples):
    return tokenizer(examples["text"], truncation=True)

In [11]:
tokenized_df = new_data.map(preprocess_function, batched=True)

Map:  48%|████▊     | 13000/26889 [00:00<00:00, 32226.42 examples/s]

Map: 100%|██████████| 6723/6723 [00:00<00:00, 41978.69 examples/s]


In [12]:
# from transformers import DataCollatorWithPadding

# data_collator = DataCollatorWithPadding(tokenizer=tokenizer, return_tensors="tf")




from transformers import DataCollatorWithPadding

data_collator = DataCollatorWithPadding(tokenizer=tokenizer)

2023-10-13 10:29:49.212220: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-10-13 10:29:50.573292: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


In [13]:
import evaluate

accuracy = evaluate.load("accuracy")

In [14]:
import numpy as np


def compute_metrics(eval_pred):
    predictions, labels = eval_pred
    predictions = np.argmax(predictions, axis=1)
    return accuracy.compute(predictions=predictions, references=labels)

In [15]:
import json


In [16]:
label2id= json.load(
    open('data/categories_refined.json', 'r')
)
label2id

{'Hobbies_and_Leisure': 0,
 'News': 1,
 'Science': 2,
 'Autos_and_Vehicles': 3,
 'Health': 4,
 'Pets_and_Animals': 5,
 'Adult': 6,
 'Computers_and_Electronics': 7,
 'Online Communities': 8,
 'Beauty_and_Fitness': 9,
 'People_and_Society': 10,
 'Business_and_Industrial': 11,
 'Reference': 12,
 'Shopping': 13,
 'Travel_and_Transportation': 14,
 'Food_and_Drink': 15,
 'Law_and_Government': 16,
 'Books_and_Literature': 17,
 'Finance': 18,
 'Games': 19,
 'Home_and_Garden': 20,
 'Jobs_and_Education': 21,
 'Arts_and_Entertainment': 22,
 'Sensitive Subjects': 23,
 'Real Estate': 24,
 'Internet_and_Telecom': 25,
 'Sports': 26}

In [17]:
id2label= {}
for key in label2id.keys():
    id2label[label2id[key]] = key
    
id2label

{0: 'Hobbies_and_Leisure',
 1: 'News',
 2: 'Science',
 3: 'Autos_and_Vehicles',
 4: 'Health',
 5: 'Pets_and_Animals',
 6: 'Adult',
 7: 'Computers_and_Electronics',
 8: 'Online Communities',
 9: 'Beauty_and_Fitness',
 10: 'People_and_Society',
 11: 'Business_and_Industrial',
 12: 'Reference',
 13: 'Shopping',
 14: 'Travel_and_Transportation',
 15: 'Food_and_Drink',
 16: 'Law_and_Government',
 17: 'Books_and_Literature',
 18: 'Finance',
 19: 'Games',
 20: 'Home_and_Garden',
 21: 'Jobs_and_Education',
 22: 'Arts_and_Entertainment',
 23: 'Sensitive Subjects',
 24: 'Real Estate',
 25: 'Internet_and_Telecom',
 26: 'Sports'}

In [18]:
from transformers import AutoModelForSequenceClassification, TrainingArguments, Trainer

model = AutoModelForSequenceClassification.from_pretrained(
    "finetuned_entity_categorical_classification/checkpoint-3346", num_labels=27, id2label=id2label, label2id=label2id
)

In [19]:
training_args = TrainingArguments(
    output_dir="finetuned_entity_categorical_classification",
    learning_rate=2e-5,
    per_device_train_batch_size=16,
    per_device_eval_batch_size=16,
    num_train_epochs=2,
    weight_decay=0.01,
    evaluation_strategy="epoch",
    save_strategy="epoch",
    load_best_model_at_end=True,
    # push_to_hub=True,
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=tokenized_df["train"],
    eval_dataset=tokenized_df["test"],
    tokenizer=tokenizer,
    data_collator=data_collator,
    compute_metrics=compute_metrics,
)

trainer.train()

You're using a DistilBertTokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.


TrainOutput(global_step=3362, training_loss=0.08880683540376008, metrics={'train_runtime': 113.5357, 'train_samples_per_second': 473.666, 'train_steps_per_second': 29.612, 'total_flos': 213673546900476.0, 'train_loss': 0.08880683540376008, 'epoch': 2.0})